# Tutorial 3 : Retrieving hourly emissions data from a specific vessel

The Ocean Data Platform's database contains hourly vessel emissions for most larger vessels. 

- Information about each vessel can be found in the "vessel_particulars" table
- Hourly vessel emissions for a given vessel can be retrieved through the get_emissions_from_vessel(mmsi) which takes the vessel's MMSI number as input


In [1]:
import os
import pandas as pd
from sqlalchemy.engine import create_engine

If run outside the Ocean Data Connector environment, the following needs to be set.

In [2]:
# Connection string has to be set if run outside the Ocean Data Connector
#os.environ['HACKATHON_DB_CONNECTION'] = 'xxxx'
try: 
    os.environ['HACKATHON_DB_CONNECTION']
except:
    print('HACKATHON_DB_CONNECTION must be set to access data')

In [3]:
engine = create_engine(os.environ['HACKATHON_DB_CONNECTION'])

## Finding the largest bulk carrier in the vessel table

In [4]:
sql=f'''
    select * from vessel_particulars
    where "ICCT_class"='Bulk carrier'
    order by "Deadweight" desc
    limit 10
    '''
df_vessel_info=pd.read_sql(sql,engine)

In [5]:
df_vessel_info.iloc[0]

LRIMOShipNo                                                    9575450
ShipName                                                   SEA QINGDAO
ShiptypeLevel5                                             Ore Carrier
YearOfBuild                                                       2012
Deadweight                                                      403880
ShipStatus                                       In Service/Commission
FlagName                                              Marshall Islands
FuelType1First                                         Distillate Fuel
LengthRegistered                                                353.52
MainEngineType                                                     Oil
MaritimeMobileServiceIdentityMMSINumber                      538004553
PropulsionType                             Oil Engine(s), Direct Drive
Speedmax                                                           0.0
Speedservice                                                      14.8
ICCT_c

## Retrieving emissions data for vessel

In [6]:
mmsi=df_vessel_info.iloc[0].MaritimeMobileServiceIdentityMMSINumber#374123000
time_from= '2021-01-01 00:00:00'
time_to= '2021-12-31 23:00:00'
sql=f'''
    select * from get_emissions_from_vessel({mmsi}) 
    where timestamp>='{time_from}' and timestamp<='{time_to}'
    order by timestamp asc
    '''
df_vessel=pd.read_sql(sql,engine)

In [7]:
df_vessel

timestamp        lat        lon  course      speed  \
0    2021-01-01 00:00:00+00:00 -38.533040  14.165680   100.4  10.900000   
1    2021-01-01 01:00:00+00:00 -38.562107  14.390187    96.2  11.400000   
2    2021-01-01 02:00:00+00:00 -38.588187  14.629760    98.7  11.400000   
3    2021-01-01 03:00:00+00:00 -38.622053  14.925360    96.4  11.300000   
4    2021-01-01 04:00:00+00:00 -38.637173  15.108400    95.9  11.500000   
...                        ...        ...        ...     ...        ...   
8736 2021-12-31 19:00:00+00:00 -25.525075  86.218615    65.1  10.500000   
8737 2021-12-31 20:00:00+00:00 -25.461897  86.388592    69.9  10.400000   
8738 2021-12-31 21:00:00+00:00 -25.391145  86.562415    63.0  10.100000   
8739 2021-12-31 22:00:00+00:00 -25.322470  86.736893    65.7  10.200000   
8740 2021-12-31 23:00:00+00:00 -25.245356  86.926863     NaN  10.266667   

      emissions_CO2  emissions_CO  emissions_SOX  emissions_N2O  \
0      7.271560e+06   6431.569014  123266.920665     361.509390   
1      8.276071e+06   7325.203437  140295.621052     411.155747   
2      8.276071e+06   7325.203437  140295.621052     411.155747   
3      8.067931e+06   7140.037153  136767.174633     400.868731   
4      8.487896e+06   7513.646916  143886.516234     421.624829   
...             ...           ...            ...            ...   
8736   6.531545e+06   5773.236204  110722.023214     324.935345   
8737   6.355105e+06   5616.271041  107730.964836     316.215058   
8738   5.845818e+06   5163.198892   99097.423326     291.044383   
8739   6.012273e+06   5311.281132  101919.212688     299.271174   
8740   6.464935e+06   5713.978486  109592.834489     321.643249   

      emissions_NOX  emissions_PM  emissions_CH4  
0     170164.507053  16921.044445     119.103130  
1     193994.758323  19270.972001     135.651916  
2     193994.758323  19270.972001     135.651916  
3     189056.990740  18784.053253     132.222910  
4     199019.917762  19766.508557     139.141610  
...             ...           ...            ...  
8736  152608.965431  15189.872980     106.911782  
8737  148423.227759  14777.112737     104.005019  
8738  136341.303780  13585.700789      95.614794  
8739  140290.163529  13975.102237      98.357058  
8740  151028.759635  15034.047131     105.814416  

[8741 rows x 12 columns]

## Plot vessel positions

In [8]:
import os
import pydeck as pdk
def plot_df(point):
    layers=[]
    if point is not None:
        point_cloud_layer = pdk.Layer(
        "PointCloudLayer",
        data=point,
        get_position=["lon", "lat"],
        get_color=["speed*20", "speed*10", "255-speed*10"],
        get_normal=[0, 0, 15],
        auto_highlight=True,
        pickable=True,
        point_size=5)
        
        layers.append(point_cloud_layer)
        layer = pdk.Layer(
            'PathLayer',
            [{'path':list(zip(point.lon,point.lat))}],
            width_min_pixels=2,
            get_color='[0, 0, 0, 150]',
        )
        layers.append(layer)

        view = pdk.data_utils.compute_view(point[["lon", "lat"]])

    
    r = pdk.Deck(layers=layers[::-1],map_style='light', 
                initial_view_state=view)

    return r

In [9]:
plot_df(df_vessel)

{"initialViewState": {"latitude": -12.494743697576213, "longitude": 34.623299952884445, "zoom": 1}, "layers": [{"@@type": "PathLayer", "data": [{"path": [[14.16568, -38.53304], [14.3901866667, -38.5621066667], [14.62976, -38.5881866667], [14.92536, -38.6220533333], [15.1084, -38.6371733333], [15.4667466667, -38.6663733333], [15.6630933333, -38.6818666667], [15.9046666667, -38.6987766667], [16.1055733333, -38.71128], [16.3706666667, -38.7303466667], [16.63696, -38.7519733333], [16.9006133333, -38.7717066667], [17.2547733333, -38.7981066667], [17.4485333333, -38.81056], [17.6972533333, -38.83336], [17.9653066667, -38.8514933333], [18.2496533333, -38.8735466667], [18.4911466667, -38.8904266667], [18.9146666667, -38.9188], [19.0469866667, -38.9284], [19.2728, -38.9472], [19.5219733333, -38.9630666667], [19.77432, -38.9822933333], [20.0491466667, -38.9988533333], [20.2837333333, -38.9979733333], [20.5255733333, -39.0008266667], [20.7774666667, -38.9988533333], [21.1103733333, -39.0000266667], [21.56048, -38.9994666667], [21.6053333333, -38.9985866667], [21.8606133333, -38.9985866667], [22.1441066667, -39.0008266667], [22.4295466667, -38.9997066667], [22.7146933333, -39.0001866667], [23.0613333333, -39.00256], [23.40184, -39.00264], [23.7271733333, -38.99856], [24.02744, -38.9994666667], [24.3117866667, -39.0010933333], [24.60712, -38.9980266667], [25.0957333333, -38.998], [25.13176, -38.99768], [25.51608, -38.9985333333], [25.66032, -38.9982666667], [25.897855, -38.9986133333], [26.1208266667, -39.0002133333], [26.3576533333, -38.99896], [26.6204533333, -38.9997333333], [26.8594666667, -38.9985066667], [27.14896, -39.0001066667], [27.36376, -39.0020266667], [27.61224, -38.99968], [28.026, -39.0016266667], [28.32416, -39.0014666667], [28.5092533333, -39.00072], [28.8427466667, -38.9986133333], [29.177315, -38.9987816667], [29.5849333333, -38.9992], [29.8333066667, -39.0024266667], [30.1195466667, -39.00032], [30.41704, -39.00032], [30.69504, -38.9984266667], [31.0651733333, -39.0003466667], [31.2811466667, -38.99928], [31.5254933333, -39.00496], [31.7800533333, -39.0046133333], [32.11856, -38.9992266667], [32.31296, -39.0004266667], [32.58128, -38.9994666667], [32.8571483333, -39.000045], [33.1302666667, -38.9993066667], [33.4104266667, -38.99864], [33.6674133333, -39.0016], [33.9316, -38.9987466667], [34.2619466667, -39.0012266667], [34.51592, -39.0005866667], [34.7692266667, -39.00048], [35.0164, -39.0036266667], [35.26112, -38.9997866667], [35.55824, -38.99992], [35.82296, -38.9992533333], [36.1172533333, -38.99904], [36.3792533333, -38.9988], [36.6678666667, -38.99736], [36.9493066667, -38.9973333333], [37.2327466667, -39.0023733333], [37.5390666667, -39.0012266667], [37.81752, -39.0019733333], [38.1102933333, -39.0031733333], [38.2583466667, -39.0032533333], [38.50248, -39.00248], [38.750285, -39.0011066667], [38.9936, -39.00144], [39.2460266667, -39.0006133333], [39.48304, -39.0012266667], [39.7337333333, -38.9992], [39.96576, -38.9997066667], [40.2186133333, -38.9923733333], [40.4561866667, -38.98424], [40.7340266667, -38.9742933333], [41.0681866667, -38.9634933333], [41.26576, -38.9534133333], [41.52536, -38.9438666667], [41.80168, -38.9351466667], [42.0492, -38.9265066667], [42.3257066667, -38.91696], [42.5958933333, -38.9040533333], [42.8675466667, -38.89256], [43.1487733333, -38.8766933333], [43.4208266667, -38.8568533333], [43.6855466667, -38.8430666667], [44.0112266667, -38.8233866667], [44.1537866667, -38.8153333333], [44.3891733333, -38.8058933333], [44.6486133333, -38.7905333333], [44.8913333333, -38.7725066667], [45.1572266667, -38.7521866667], [45.4183733333, -38.73264], [45.6875466667, -38.7137066667], [45.9694933333, -38.6924266667], [46.2637333333, -38.6654133333], [46.5669333333, -38.6418933333], [47.0728533333, -38.60344], [47.1699466667, -38.5944], [47.502, -38.5626133333], [47.68856, -38.54304], [47.9450666667, -38.5230666667], [48.2078133333, -38.49368], [48.4415466667, -38.4726133333], [48.69968, -38.44688